In [10]:
import osmnx as ox
import pandas as pd
import numpy as np
import folium

In [14]:
# Определим функцию для выполнения запроса
def osm_query(tag, city):
    # Получаем объекты с нужным тегом в заданном городе
    gdf = ox.geometries_from_place(city, tag).reset_index()
    gdf['city'] = np.full(len(gdf), city.split(',')[0])
    gdf['object'] = np.full(len(gdf), list(tag.keys())[0])
    gdf['type'] = np.full(len(gdf), tag[list(tag.keys())[0]])
    gdf = gdf[['city', 'object', 'type', 'geometry']]
    print(f"Found {gdf.shape[0]} results for {tag} in {city}")
    return gdf

# Тег для поиска всех кафе
tag = {'amenity': 'cafe'}


# все что в голову взбрело
# tags = [
#         {'building' : 'apartments'}, {'building' : 'detached'}, 
#         {'building' : 'dormitory'}, {'building' : 'hotel'}, 
#         {'building' : 'house'}, {'building' : 'semidetached_house'}, 
#         {'building' : 'terrace'},  {'building' : 'commercial'},
#         {'building' : 'office'},  {'building' : 'terrace'},  
#         {'building' : 'terrace'}, {'building':'retail'}, 
#         {'building':'train_station'},
#         {'highway' : 'bus_stop'}, {'footway':'crossing'},
#         {'amenity':'cafe'}, {'amenity':'fast_food'}, 
#         {'amenity':'restaurant'}, {'amenity':'college'}, 
#         {'amenity':'language_school'},  {'amenity':'school'},  
#         {'amenity':'university'},  {'amenity':'atm'},  
#         {'amenity':'bank'},  {'amenity':'clinic'},  
#         {'amenity':'hospital'},  {'amenity':'pharmacy'},  
#         {'amenity':'theatre'},  {'amenity':'townhall'},  
#         {'amenity':'bench'}, 
#        ]

# торговые точки
# tags = [ 
#     {'shop': 'supermarket'},
#     {'shop': 'convenience'},
#     {'shop': 'bakery'},
#     {'shop': 'greengrocer'},
#     {'shop': 'butcher'},
#     {'shop': 'deli'},
#     {'shop': 'organic'},
#     {'shop': 'seafood'},
#     {'shop': 'alcohol'},
#     {'shop': 'beverages'},
#     {'shop': 'cheese'}
# ]

city = 'Москва, Россия'

# Выполним запрос и получим все кофейни в указанном городе
cafes_gdf = osm_query(tag, city)

#cafes_gdf = cafes_gdf.to_crs("EPSG:3857")
cafes_gdf['lat'] = cafes_gdf['geometry'].centroid.y
cafes_gdf['lon'] = cafes_gdf['geometry'].centroid.x

cafes_gdf.head()

/tmp/ipykernel_30/791234836.py:4: FutureWarning: The `geometries` module and `geometries_from_X` functions have been renamed the `features` module and `features_from_X` functions. Use these instead. The `geometries` module and function names are deprecated and will be removed in the v2.0.0 release. See the OSMnx v2 migration guide: https://github.com/gboeing/osmnx/issues/1123
  gdf = ox.geometries_from_place(city, tag).reset_index()


Found 4582 results for {'amenity': 'cafe'} in Москва, Россия


/tmp/ipykernel_30/791234836.py:57: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  cafes_gdf['lat'] = cafes_gdf['geometry'].centroid.y
/tmp/ipykernel_30/791234836.py:58: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  cafes_gdf['lon'] = cafes_gdf['geometry'].centroid.x


city   object  type                   geometry        lat        lon
0  Москва  amenity  cafe  POINT (37.52715 55.65170)  55.651703  37.527154
1  Москва  amenity  cafe  POINT (37.68888 55.70522)  55.705221  37.688884
2  Москва  amenity  cafe  POINT (37.67871 55.78971)  55.789705  37.678715
3  Москва  amenity  cafe  POINT (37.78577 55.69769)  55.697688  37.785774
4  Москва  amenity  cafe  POINT (37.57299 55.68667)  55.686673  37.572991

In [15]:
map_center = [55.7558, 37.6173]  # Координаты Москвы
mymap = folium.Map(location=map_center, zoom_start=12)

for idx, row in cafes_gdf.iterrows():
    folium.Marker(
        location=[row['lat'], row['lon']],
        popup=f"Cafe: {row['type']}",
        icon=folium.Icon(color="blue", icon="info-sign")
    ).add_to(mymap)

mymap